<h1>Computation of $\mathcal{GT}_1(G)$</h1>

<em>Pierre Guillot</em>

This computes the group $\mathcal{GT}_1(G)$, described in my paper <em>The Grothendieck-Teichmüller group of a finite group and $G$-dessins d'enfants</em>. 

In order to use and modify the script, you first need to:
<ul><li>create an accound on SageMathCloud, if you haven't got one already, </li>
<li>create at least one "project" on SageMathCloud.</li></ul>

Then you can click on "Copy Jupyter Notebook to your project...", in the top left hand corner.

Alternatively, if you have a recent version of Sage installed, with the Jupyter Notebook working, you can click on "Download".

In [1]:
IsContained= libgap.function_factory("\in")

In [2]:
class GT1:
    
    def __init__(self, G, verbose= False, very_verbose= False):
        
        self.G= G
        self.verbose= verbose or very_verbose
        self.very_verbose= very_verbose
        
    def compute_cover_group(self):
        
        if self.verbose:
            print "*** computing cover"
        
        ##product group
        GG= self.G.DirectProduct(self.G)
        i1= GG.Embedding(1)
        i2= GG.Embedding(2)
        p1= GG.Projection(1)
        p2= GG.Projection(2)

        ##automorphism group of G
        autG= self.G.AutomorphismGroup()
        #convert the elements of autG into automorphisms of GG
        gensautG= autG.GeneratorsOfGroup()
        gensGG= GG.GeneratorsOfGroup()
        imgs= []
        for phi in gensautG:
            phi_on_gens= [ (p1*phi*i1).Image(gh) * (p2*phi*i2).Image(gh) for gh in gensGG  ]
            phiGG= GG.GroupHomomorphismByImages(GG, gensGG, phi_on_gens)
            imgs.append(phiGG)
        #using this, embed autG in autGG...
        diagautG= libgap.Group(imgs)

        ### classes of pairs in G
        classes= diagautG.OrbitsDomain(GG)

        if self.very_verbose:
            print len(classes), "classes of pairs"

        def is_generating_pair(C):
            pair= C[0]
            x=  p1.Image(pair)
            y=  p2.Image(pair)

            return self.G.Subgroup([x, y]) == self.G

        gens_classes= [ C for C in classes if is_generating_pair(C) ]
        r= len(gens_classes)
        
        if self.very_verbose:
            print r,"of them generate G"

        ###build G^r and then GB
        Gr= libgap.DirectProduct([ self.G for i in range(r) ])
        inj= [ Gr.Embedding(i) for i in [1..r] ]
        self.x= prod([ (p1*inj[i]).Image(gens_classes[i][0])  for i in range(r)  ])
        self.y= prod([ (p2*inj[i]).Image(gens_classes[i][0])  for i in range(r)  ])
        self.GB= Gr.Subgroup([self.x, self.y])


    def compute_automorphisms(self):
        if self.verbose:
            print "*** computing representatives for GT1"
            
        # for convenience
        GB= self.GB
        x= self.x
        y= self.y 
        one= GB.Identity()
        
        ### the centralizers 
        Cx= GB.Centralizer(x)
        Cy= GB.Centralizer(y)

        ### find the double cosets
        doubles= GB.DoubleCosets(Cx, Cy)
        if self.very_verbose:
            print "found", len(doubles), "double cosets"
        wait= len(doubles)
        
        ### prepare theta and delta
        theta= GB.GroupHomomorphismByImages(GB, [x, y], [y, x])
        delta= GB.GroupHomomorphismByImages(GB, [x, y], [y^(-1)*x^(-1), y])

        ### do all the tests !
        
        self.auts= []
        
        for i, C in enumerate(doubles):
            if self.very_verbose:
                print "coset", i+1, "out of", wait
            #take a representative
            c= C.Representative()
            xp= x^c
            
            #first test: <x^c, y> is all of GB
            GBp= GB.Subgroup([xp, y])
            if GBp != GB:
                continue # try next C
       
            #second test: commutation with theta
            ct= c^theta
            if not IsContained(one, Cx.DoubleCoset(c*ct, Cy^ct)):
                continue
     
            #third test: automorphism is actually well-defined
            phi= GB.GroupHomomorphismByImages(GB, [x, y], [xp, y])
            if phi == libgap.eval("fail"):
                continue

            #fourth test: commutation with delta
            if not libgap.IsInnerAutomorphism( phi*delta*phi^(-1)*delta^(-1)):
                continue
            
            #if we're here, all the tests have been passed!
            if self.very_verbose:
                print "found an element in GT1(G) !"
                
            self.auts.append(phi)

  

In [4]:
#G= libgap.SmallGroup(64,34)
G= libgap.PSL(2,2)

In [5]:
which_group(G)

"S3"

In [6]:
gt= GT1(G, very_verbose= True)

In [7]:
gt.compute_cover_group()

*** computing cover
11 classes of pairs
3 of them generate G


In [8]:
gt.compute_automorphisms()

*** computing representatives for GT1
found 3 double cosets
coset 1 out of 3
found an element in GT1(G) !
coset 2 out of 3
found an element in GT1(G) !
coset 3 out of 3


In [9]:
gt.auts

[[ (2,3)(5,6)(7,8,9), (1,2)(4,5,6)(8,9) ] -> [ (2,3)(5,6)(7,8,9), (1,2)(4,5,6)(8,9) ],
 [ (2,3)(5,6)(7,8,9), (1,2)(4,5,6)(8,9) ] -> [ (2,3)(5,6)(7,9,8), (1,2)(4,5,6)(8,9) ]]